In [1]:
from huggingface_hub import HfApi
import math
!huggingface-cli login --token hf_xxxx
def get_folder_subset(repo_id, start_percent, end_percent, repo_type="dataset"):
    api = HfApi()

    # List the contents of the repository
    repo_contents = api.list_repo_files(repo_id, repo_type=repo_type)

    # Filter for files inside the "data" directory
    data_contents = [file for file in repo_contents if file.startswith("data/")]

    # Get unique folders inside "data"
    folders_in_data = sorted(set(file.split('/')[1] for file in data_contents if file.count('/') > 1))
    
    total_folders = len(folders_in_data)
    start_index = math.floor(total_folders * start_percent / 100)
    end_index = math.floor(total_folders * end_percent / 100)

    selected_folders = folders_in_data[start_index:end_index]

    print(f"Total folders: {total_folders}")
    print(f"Selected folders ({start_percent}% - {end_percent}%): {len(selected_folders)}")
    print("Folders:", ', '.join(selected_folders))

    # Return files from selected folders
    selected_files = [file for file in data_contents if file.split('/')[1] in selected_folders]
    return selected_files

# Replace with the actual repo_id
repo_id = "litagin/moe-speech"

# Example usage:
# First 25%
# first_quarter = get_folder_subset(repo_id, 0, 25)

# # Second 25%
#second_quarter = get_folder_subset(repo_id, 25, 50)

# # Third 25%
third_quarter = get_folder_subset(repo_id, 50, 75)

# # Last 25%
# last_quarter = get_folder_subset(repo_id, 75, 100)


The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /home/austin/.cache/huggingface/token
Login successful
Total folders: 473
Selected folders (50% - 75%): 118
Folders: 773a4156, 7787d8bf, 78024d52, 780c767e, 78a17f40, 78ddc745, 79a9f817, 79b0d13c, 79ff88ce, 7a63c040, 7aa5ec7f, 7b3d6f79, 7bc60e34, 7cf5370c, 7d23dc35, 7d557804, 7d9fed60, 7da6e5dd, 7e74d475, 7f563200, 7fa77e7c, 80e000b3, 82917a7d, 8340aaf6, 84be23bd, 84d1e0bf, 86a62c68, 86b2eb0e, 88ea6529, 89374c0b, 8a601bf6, 8b6e7173, 8d2b2495, 8d6eccd0, 8da3217d, 8e1072e6, 8f8acabb, 8fd9edef, 8fe123c6, 90d21566, 90f28db9, 90fa05fd, 91539726, 915f3667, 917e0da2, 917feebd, 91c32dcd, 93443a40, 93dda15e, 940de876, 95719ea1, 95c3bdd8, 95c67421, 96d8dcb4, 978de897, 99b5eb16, 9a3063e7, 9c125949, 9d05be3b, 9

In [2]:
import io
import sys
import time
import threading
from IPython import get_ipython

def start_logging(log_file_path='cell_75%_output.log', interval=5):
    # Create a custom output stream
    class LogStream(io.StringIO):
        def __init__(self, filename):
            super().__init__()
            self.filename = filename
        
        def write(self, text):
            super().write(text)
            with open(self.filename, 'a') as f:
                f.write(text)

    # Create the log stream
    log_stream = LogStream(log_file_path)

    # Redirect stdout and stderr to the log stream
    sys.stdout = log_stream
    sys.stderr = log_stream

    # Function to save the current output
    def save_output():
        while True:
            time.sleep(interval)
            log_stream.flush()

    # Start the logging in a separate thread
    logging_thread = threading.Thread(target=save_output, daemon=True)
    logging_thread.start()

    print(f"Logging started. Output will be saved to {log_file_path} every {interval} seconds.")

# Start logging
start_logging()

In [ ]:
from huggingface_hub import hf_hub_download
from tqdm import tqdm
import os
import time

def download_dataset(repo_id, local_dir, file_list, num_retries=10, retry_interval=15):
    # Check if the files are already downloaded
    downloaded_files = []
    for root, _, files in os.walk(local_dir):
        for file in files:
            downloaded_files.append(os.path.relpath(os.path.join(root, file), local_dir))

    # Download files
    for file_path in tqdm(file_list):
        local_file_path = os.path.join(local_dir, file_path)
        os.makedirs(os.path.dirname(local_file_path), exist_ok=True)

        # Check if the file is already downloaded
        if file_path in downloaded_files:
            print(f"Skipping already downloaded file: {file_path}")
            continue

        # Retry download
        for retry_count in range(num_retries):
            try:
                # Download the file
                hf_hub_download(
                    repo_id=repo_id,
                    filename=file_path,
                    repo_type="dataset",
                    local_dir=local_dir,
                    local_dir_use_symlinks=False
                )
                print(f"Successfully downloaded: {file_path}")
                break  # Exit the loop if download is successful
            except Exception as e:
                print(f"Error downloading {file_path}. Retrying in {retry_interval} seconds... ({retry_count+1}/{num_retries})")
                if retry_count == num_retries - 1:
                    print(f"Failed to download {file_path} after {num_retries} attempts.")
                else:
                    time.sleep(retry_interval)

# Usage
repo_id = "litagin/moe-speech"
local_dir = "/home/austin/disk2/llmvcs/tt/stylekan/Data/"

download_dataset(repo_id, local_dir, third_quarter)

773a4156_0000.wav:   0%|          | 0.00/636k [00:00<?, ?B/s]

773a4156_0001.wav:   0%|          | 0.00/822k [00:00<?, ?B/s]

773a4156_0002.wav:   0%|          | 0.00/488k [00:00<?, ?B/s]

773a4156_0003.wav:   0%|          | 0.00/307k [00:00<?, ?B/s]

773a4156_0004.wav:   0%|          | 0.00/298k [00:00<?, ?B/s]

...

7d9fed60_436.wav:   0%|          | 0.00/205k [00:00<?, ?B/s]

7d9fed60_437.wav:   0%|          | 0.00/372k [00:00<?, ?B/s]

7d9fed60_438.wav:   0%|          | 0.00/633k [00:00<?, ?B/s]

7d9fed60_439.wav:   0%|          | 0.00/597k [00:00<?, ?B/s]

7d9fed60_440.wav:   0%|          | 0.00/303k [00:00<?, ?B/s]